Mathematical Model of the Inverted Pendulum


1. System Description

An inverted pendulum consists of:

          A cart of mass M moving horizontally

         A pendulum of mass m and length L (center of mass at L/2)

         An external force F applied to the cart



2. Governing Equations
Derived using Lagrangian mechanics, the nonlinear dynamics :


Cart Motion (Horizontal)

           (M + m)ẍ + bẋ + mLθ̈cos θ - mLθ̇²sin θ = F


Pendulum Motion (Rotational)

           (I + mL²)θ̈ + mgL sin θ = -mLẍ cos θ

 
     Where:

         I = (1/12)mL² (moment of inertia for a thin rod)

          b: Friction coefficient of the cart


3. Linearized Model (Small-Angle Approximation)

          For θ ≈ 0 (upright position):
 
           sin θ ≈ θ

            cos θ ≈ 1

            θ̇² ≈ 0

       Simplified equations:

          (M + m)ẍ + bẋ + mLθ̈ = F

          (I + mL²)θ̈ + mgLθ = -mLẍ


4. State-Space Representation

Define states:

            x = [x, ẋ, θ, θ̇]ᵀ

Linearized state-space model:

          ẋ = Ax + Bu,  where u = F



System matrices:


          A = ⎡  0      1       0        0    ⎤
             
              ⎢  0    -b/M   -mg/M      0    ⎥

              ⎢  0      0       0        1    ⎥
    
              ⎣  0   bML   (M+m)g/ML   0    ⎦
    


         B = ⎡   0   ⎤

             ⎢  1/M  
    
             ⎢   0   ⎥
    
             ⎣ -1/ML ⎦




5. Control Law (PID Controller)

         To stabilize the pendulum upright:

             F = Kₚ(θdesired - θ) + Kd θ̇ + Ki ∫(θdesired - θ) dt

       where θdesired = π (vertical position)

Control parameters:

       Kₚ: Proportional gain

       Kd: Derivative gain

       Ki: Integral gain



6. Key Assumptions

       Pendulum is a rigid rod with uniform mass distribution
       No friction at the pivot point
       Small-angle approximation valid near θ = π
       Cart moves on a frictionless horizontal track (except for damping b)
       External disturbances are negligible




7. Non-Dimensional Parameters

        Natural frequency: ωₙ = √(g/L)

        Damping ratio: ζ = b/[2√((M+m)gL)]

System stability:

       Stable when ζ > 0 and control gains are properly tuned

     Unstable open-loop system requires active control


In [2]:
import numpy as np
from scipy.integrate import odeint
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from matplotlib.patches import Rectangle

In [3]:
# System parameters
M = 1.0      # Mass of the cart [kg]
m = 0.3      # Mass of the pendulum [kg]
l = 0.5      # Length to pendulum center of mass [m]
g = 9.81     # Gravity [m/s²]
b = 0.1      # Cart friction coefficient [N·s/m]


In [4]:
# Simulation parameters
dt = 0.05    # Time step [s]
t_max = 10.0 # Simulation duration [s]
t = np.arange(0, t_max, dt)

In [5]:
# Initial conditions [x, x_dot, theta, theta_dot]
initial_state = [0, 0, np.pi + 0.1, 0]  # Start nearly inverted

In [6]:
# Control parameters (simple proportional control)
Kp = 50.0    # Proportional gain

def inverted_pendulum(state, t):
    """Differential equations for the inverted pendulum system"""
    x, x_dot, theta, theta_dot = state
    
    # Control force (simple proportional control to keep pendulum upright)
    F = Kp * (np.pi - theta)  # Try to maintain theta=pi (upright)
    
    # Intermediate variables
    sin_theta = np.sin(theta)
    cos_theta = np.cos(theta)
    total_mass = M + m
    denom = (M + m * sin_theta**2)
    
    # Derivatives
    x_ddot = (F + m*l*theta_dot**2*sin_theta - b*x_dot - m*g*cos_theta*sin_theta) / denom
    theta_ddot = (-F*cos_theta - m*l*theta_dot**2*sin_theta*cos_theta + total_mass*g*sin_theta + b*x_dot*cos_theta) / (l * denom)
    
    return [x_dot, x_ddot, theta_dot, theta_ddot]


In [7]:
# Solve the differential equations
states = odeint(inverted_pendulum, initial_state, t)

# Extract the solution
x = states[:, 0]
theta = states[:, 2]

In [8]:
# Animation setup
fig, ax = plt.subplots(figsize=(10, 6))
ax.set_xlim(-2, 2)
ax.set_ylim(-0.7, 1.5)
ax.set_aspect('equal')
ax.grid()

# Create cart and pendulum
cart_width = 0.4
cart_height = 0.2
cart = Rectangle((x[0] - cart_width/2, -cart_height/2), cart_width, cart_height, 
                 fc='blue', ec='black')
ax.add_patch(cart)

pendulum, = ax.plot([x[0], x[0] + l*np.sin(theta[0])], 
                    [0, -l*np.cos(theta[0])], 'r-', lw=2)
bob = ax.plot([x[0] + l*np.sin(theta[0])], [-l*np.cos(theta[0])], 'ro', ms=10)[0]
time_text = ax.text(0.02, 0.95, '', transform=ax.transAxes)

def init():
    """Initialize animation"""
    cart.set_xy((x[0] - cart_width/2, -cart_height/2))
    pendulum.set_data([x[0], x[0] + l*np.sin(theta[0])], 
                      [0, -l*np.cos(theta[0])])
    bob.set_data([x[0] + l*np.sin(theta[0])], [-l*np.cos(theta[0])])
    time_text.set_text('')
    return cart, pendulum, bob, time_text

def animate(i):
    """Update animation for frame i"""
    cart_x = x[i] - cart_width/2
    cart.set_xy((cart_x, -cart_height/2))
    
    pendulum_x = [x[i], x[i] + l*np.sin(theta[i])]
    pendulum_y = [0, -l*np.cos(theta[i])]
    pendulum.set_data(pendulum_x, pendulum_y)
    
    bob.set_data([x[i] + l*np.sin(theta[i])], [-l*np.cos(theta[i])])
    
    time_text.set_text(f'Time = {t[i]:.2f}s\nAngle = {np.degrees(theta[i] - np.pi):.1f}°')
    
    # Adjust view if cart moves too far
    ax.set_xlim(x[i] - 2, x[i] + 2)
    
    return cart, pendulum, bob, time_text

# Create animation
ani = animation.FuncAnimation(fig, animate, frames=len(t),
                              init_func=init, blit=True, interval=dt*1000)

plt.title('Inverted Pendulum Simulation')
plt.xlabel('Position [m]')
plt.ylabel('Height [m]')
plt.close()  # Close the static plot to only show animation

# To save the animation (requires ffmpeg)
# ani.save('inverted_pendulum.mp4', writer='ffmpeg', fps=1/dt)

# Display the animation
from IPython.display import HTML
HTML(ani.to_jshtml())